In [66]:
from importlib import reload
import utils
from os import makedirs
from pathlib import Path
from IPython.display import Audio
from torch.nn import functional as F
import torch

# Splitting Datasets
splitting all files into train, test, and validation

In [2]:
files = utils.get_all_files_from('clips')
train_folder = "clips-train"
test_folder = "clips-test"
validation_folder = "clips-validation"

files = list(set(files))
n = len(files)
n_test = int(0.01 * n)
n_validation = int(0.05 *n)

validation_files = files[:n_validation]
test_files = files[-n_test:]
train_files = files[n_validation:-n_test]

(n, n_test, n_validation)
# list(map(len, (validation_files, test_files, train_files)))


(0, 0, 0)

In [3]:
def move_file_to_folder(file, dest_dir):
    Path(file).rename(Path(dest_dir) / Path(file).stem)


In [25]:
makedirs(Path(train_folder), exist_ok=True)
makedirs(Path(test_folder, exist_ok=True))
makedirs(Path(validation_folder, exist_ok=True))

for file in train_files:
    move_file_to_folder(file, train_folder)
for file in test_files:
    move_file_to_folder(file, test_folder)
for file in validation_files:
    move_file_to_folder(file, validation_folder)

# Making sure all files are of equal length

In [ ]:
from torch.nn.utils.rnn import pad_sequence

def get_slices(waveform, numSamples):
    size = waveform.shape[-1]
    slices = []
    for channel in range(waveform.shape[0]):
        idx = numSamples
        while idx < size:
            slices.append((channel, idx-numSamples, idx))
            idx += numSamples
        slices.append((channel, idx-numSamples, size))
        return slices

def return_padded_sequences(waveform, numSamples):
    return pad_sequence(wf[channel, start:end] for channel, start, end in get_slices(waveform, numSamples))
    
        

seq = return_padded_sequences(wf, 96000).transpose(0,1)
for each_wave in seq:
    print(each_wave.unsqueeze(0).shape)
file1 = seq[0].unsqueeze(0)

        

torch.Size([1, 96000])
torch.Size([1, 96000])


In [4]:
files = utils.get_all_files_from('clips-test')
file = files[0]

# Saving Equal Length File Somewhere Else

In [81]:
from torch.nn.utils.rnn import pad_sequence

def get_slices(waveform, numSamples):
    size = waveform.shape[-1]
    slices = []
    for channel in range(waveform.shape[0]):
        idx = numSamples
        while idx < size:
            slices.append((channel, idx-numSamples, idx))
            idx += numSamples
        slices.append((channel, idx-numSamples, size))
        return slices

def return_padded_sequences_1(waveform, numSamples):
    yield torch.zeros([numSamples])
    for channel, start, end in get_slices(waveform, numSamples):
        padding = numSamples - (end - start)
        yield F.pad(wf[channel, start:end], [0, padding])

def return_padded_sequences(waveform, numSamples):
    return pad_sequence(return_padded_sequences_1(waveform, numSamples)).transpose(0,1)[1:]

def thing_to_do(folder, next_folder, limit=True):
    import os
    Path(next_folder).mkdir(parents=True, exist_ok=True)
    i = 0
    for file in Path(folder).glob("*"):
        waf, _ = torchaudio.load(file)
        sequence = return_padded_sequences(waf, 96000)
        for j, wf in enumerate(sequence):
            destination = Path(next_folder) / Path(f"{file.stem}_{j}.mp3")
            print(file, waf.shape, "to" , destination, wf.shape)
            torchaudio.save(destination, wf.unsqueeze(0), sample_rate=32000)
            i += 1
            if i > 10 and limit:
                break
        else:
            continue 
        break

# thing_to_do("clips-test", "clips")

thing_to_do("clips-test", "c/test", limit=False)
thing_to_do("clips-train", "c/train", limit=False)
thing_to_do("clips-validation", "c/validation", limit=False)

clips-test/common_voice_en_39312895 torch.Size([1, 154368]) to c/test/common_voice_en_39312895_0.mp3 torch.Size([96000])
clips-test/common_voice_en_39312895 torch.Size([1, 154368]) to c/test/common_voice_en_39312895_1.mp3 torch.Size([96000])
clips-test/common_voice_en_39229160 torch.Size([1, 89856]) to c/test/common_voice_en_39229160_0.mp3 torch.Size([96000])
clips-test/common_voice_en_38739549 torch.Size([1, 146304]) to c/test/common_voice_en_38739549_0.mp3 torch.Size([96000])
clips-test/common_voice_en_38739549 torch.Size([1, 146304]) to c/test/common_voice_en_38739549_1.mp3 torch.Size([96000])
clips-test/common_voice_en_39188953 torch.Size([1, 203904]) to c/test/common_voice_en_39188953_0.mp3 torch.Size([96000])
clips-test/common_voice_en_39188953 torch.Size([1, 203904]) to c/test/common_voice_en_39188953_1.mp3 torch.Size([96000])
clips-test/common_voice_en_39188953 torch.Size([1, 203904]) to c/test/common_voice_en_39188953_2.mp3 torch.Size([96000])
clips-test/common_voice_en_393343

KeyboardInterrupt: 